In [188]:
import pandas as pd
import folium
import time
import re
import matplotlib.pyplot as plt
import seaborn as sns
sns.set()
from folium.plugins import MarkerCluster
from tqdm.notebook import tqdm

In [189]:
%%capture
%%tqdm.pandas()

In [190]:
isd = pd.read_csv('ISD Data.csv')
df = pd.read_csv('listings.csv')
df.host_name = df.host_name.apply(lambda x: str(x).replace('Sonder (Boston)', 'Sonder'))

In [191]:
isd = pd.read_csv('ISD Data.csv')
def parse_license_num(l):
    return (''.join(re.findall('[\d]*', str(l).split('\n')[0]))) or 0
isd['license_num'] = isd['License #'].apply(parse_license_num).astype(int)
df['license_num'] = df['license'].apply(parse_license_num).astype(int)

In [192]:
for air_row in tqdm(df.index):
    
    l = df.loc[air_row, 'license']
    
    if str(l)=='nan':
        df.loc[air_row, 'isd_status'] = 'No license claimed on Airbnb'
    elif 'hospitals' in l:
        df.loc[air_row, 'isd_status'] = "Exemption claimed (hospital contract)"
    elif 'business' in l:
        df.loc[air_row, 'isd_status'] = "Exemption claimed (executive suite)"
    elif 'hotel' in l:
        df.loc[air_row, 'isd_status'] = "Exemption claimed (hotel/motel)"
    else:
        air_license = df.loc[air_row, 'license_num']
        found=False
        for ref_row in isd.index:
            isd_license = isd.loc[ref_row, 'license_num']
            if air_license==isd_license:
                df.loc[air_row, 'isd_status'] = isd.loc[ref_row, 'Status'] 
                found = True
                break
        if not found:
            df.loc[air_row, 'isd_status'] = 'Fabricated'

In [193]:
status_dict = {
     'No license claimed on Airbnb': 'darkred',
    
     'Exemption claimed (hospital contract)': 'orange',
     'Exemption claimed (executive suite)': 'orange',
     'Exemption claimed (hotel/motel)': 'orange',

     'Fabricated': 'red',
     'Expired': 'red',
     'Inactive': 'red',
     'Void': 'red',
     'Revoked': 'red',
    
     'Active': 'green',
}

In [194]:
def poptext(row_idx): # for listings
    base_html = """
    <div style="font-family:Arial">
        <div style="font-size:.9em">
            <div style='font-size: .9em; margin-bottom:8px'>
                <a href='%s' target='blank'>Listing <b>%s</b> </a>
            </div>
            <div style='margin-bottom:8px'>
                ISD Status: <b>%s</b>
            </div>
            <div style='font-size: .9em; margin-bottom:5px'>
                Host: <b>%s</b>
            </div>
        </div>
    </div>
    """
    html=base_html % (
            df.loc[row_idx, 'listing_url'],
            df.loc[row_idx, 'id'],
            df.loc[row_idx, 'isd_status'],
            df.loc[row_idx, 'host_name'],
            )
    if 'Exempt' in df.loc[row_idx, 'isd_status']:
        height = "110px"
    else: height = '80px'
    iframe = folium.IFrame(html=html, width='200px', height=height)
    popup = folium.Popup(iframe, max_width=2650,)
    return popup

In [129]:
poptext

<function __main__.poptext(row_idx)>

In [201]:
host_name = 'Sonder'

m = folium.Map(location=[42.361145, -71.057083], tiles=None, zoom_start=13)
folium.TileLayer('cartodbpositron', control=False).add_to(m) # hide "all" button

for status, color in status_dict.items():

    status_data = df[(df.isd_status==status) ]#& (df.host_name==host_name)]

    globals()[f'fg{status}'] = folium.FeatureGroup(name=f'{status} ({len(status_data)})',
                                    show=True, control=True)
    m.add_child(globals()[f'fg{status}'])
    for row in status_data.index:
        folium.vector_layers.Circle(
                        [status_data.loc[row, 'latitude'], 
                         status_data.loc[row, 'longitude']],
                        color = color,
                        popup = poptext(row),
                        radius = 10, fill=True, opacity=.65,
                        fill_color=color,
        ).add_to(globals()[f'fg{status}'])   

folium.LayerControl(collapsed=True).add_to(m)

legend_html = f"""
     <div style="
     position: fixed; z-index:699; 
     bottom: 20px; left: 20px; width: 330px; height: 150px; 
     background-color:rgba(255, 255, 255, 1);
     padding: 15px;
     font-size:14px;">
        <span style='margin-bottom:3px'><b>Legend:</b> License status</span><br>
        <span style='font-size:.9em; margin-bottom:5px'>Airbnb data verified with Boston ISD registry</span><br>
        
        <i class="fa fa-circle"
        style="font-size:16px; color:#96191B; margin-right:3px"></i>
        No license claimed on Airbnb
        <br>
        
         <i class="fa fa-circle"
        style="font-size:16px; color:#F20B11; margin-right:3px"></i>
        Fabricated/Void/Inactive/Expired/Revoked 
        <br>
        
         <i class="fa fa-circle"
        style="font-size:16px; color:#FDA40A; margin-right:3px"></i>
        Exemption claimed
        <br>
        
         <i class="fa fa-circle"
        style="font-size:16px; color:#1B8A1D; margin-right:3px"></i>
        Active
        <br>
        
        
     </div>

      </div> """
m.get_root().html.add_child(folium.Element( legend_html ))

title = f"""
     <div style="
     position: fixed; z-index:699; 
     top: 10px; left: 50px; width: 485px; height: 50px; 
     background-color:rgba(255, 255, 255, 1);
     padding: 10px;">
        <div style='margin-bottom:4px; font-size:20px;'>
        <b>STR License Status of Airbnb Listings in Boston</b></div>
     </div>
      </div> """
m.get_root().html.add_child(folium.Element( title ))

updated = f"""
     <div style="
     position: fixed; z-index:699; 
     bottom: 18px; right: 0px; width: 360px; height: 28px; 
     background-color:rgba(255, 255, 255, .5);
     padding: 6px;
     font-size:12px">
        Sources: insideairbnb.com (8/31/2020) & Boston ISD (8/5/2020)</div>"""
m.get_root().html.add_child(folium.Element( updated ))

m

In [202]:
m.save('all_listing_licenses.html')